In [1]:
import pandas as pd
import torch
from torch.autograd import Variable
import torch.nn.functional as F
from torch import nn
from torch.utils.data import DataLoader, TensorDataset
from imblearn.over_sampling import SMOTE
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import confusion_matrix

In [2]:
# read csv
# https://research.unsw.edu.au/projects/unsw-nb15-dataset
# According to the website above csv is wrongly saved, so I change the name
# The number of records in the training set is 175,341 records and the testing set is 82,332 records from the different types, attack and normal.
df = pd.read_csv('../Data/UNSW_NB15_testing-set.csv')

In [3]:
# nominal to numeric of data
# proto                 object
# service               object
# state                 object

# proto to numeric
# proto_mapping = {'xxx':2, 'xxx':1, 'xxx':0}
# data['proto'] = data['proto'].map(proto_mapping)

# proto to numeric
proto_le = LabelEncoder()
df['proto'] = proto_le.fit_transform(df['proto'])
 
# service to numeric
service_le = LabelEncoder()
df['service'] = service_le.fit_transform(df['service'])

# state to numeric
state_le = LabelEncoder()
df['state'] = state_le.fit_transform(df['state'])

# nominal to numeric of data
# attack_cat            object

# target to numeric
attack_cat_le = LabelEncoder()
df['attack_cat'] = attack_cat_le.fit_transform(df['attack_cat'])

df.head(10)

id       dur  proto  service  state  spkts  dpkts  sbytes  dbytes  \
0   1  0.121478    113        0      2      6      4     258     172   
1   2  0.649902    113        0      2     14     38     734   42014   
2   3  1.623129    113        0      2      8     16     364   13186   
3   4  1.681642    113        3      2     12     12     628     770   
4   5  0.449454    113        0      2     10      6     534     268   
5   6  0.380537    113        0      2     10      6     534     268   
6   7  0.637109    113        0      2     10      8     534     354   
7   8  0.521584    113        0      2     10      8     534     354   
8   9  0.542905    113        0      2     10      8     534     354   
9  10  0.258687    113        0      2     10      6     534     268   

        rate  ...  ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
0  74.087490  ...                 1               1             0           0   
1  78.473372  ...                 1               2             0           0   
2  14.170161  ...                 1               3             0           0   
3  13.677108  ...                 1               3             1           1   
4  33.373826  ...                 1              40             0           0   
5  39.417980  ...                 1              40             0           0   
6  26.683033  ...                 1              40             0           0   
7  32.593026  ...                 1              40             0           0   
8  31.313031  ...                 1              40             0           0   
9  57.985135  ...                 1              40             0           0   

   ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  attack_cat  \
0                 0           1           1                0           6   
1                 0           1           6                0           6   
2                 0           2           6                0           6   
3                 0           2           1                0           6   
4                 0           2          39                0           6   
5                 0           2          39                0           6   
6                 0           1          39                0           6   
7                 0           3          39                0           6   
8                 0           3          39                0           6   
9                 0           3          39                0           6   

   label  
0      0  
1      0  
2      0  
3      0  
4      0  
5      0  
6      0  
7      0  
8      0  
9      0  

[10 rows x 45 columns]

In [4]:
df_train, df_test = train_test_split(df, test_size=0.3, random_state=0)

In [5]:
#df_train.dtypes
df_train.shape

(122738, 45)

In [6]:
data_train = df_train.drop(['id', 'label', 'attack_cat'], axis=1)
label_train = df_train.iloc[:,-2]
data_train.head(10)

dur  proto  service  state  spkts  dpkts  sbytes  dbytes  \
41479   0.581798    113        0      2     10      6     588     268   
174119  0.000009    119        2      3      2      0     114       0   
39585   0.294033    113        4      2      8     12     424    8824   
23269   0.001059    119        2      0      2      2     146     178   
35227   1.433471    113        3      2     52     54    2934    3742   
157804  0.000003    119        2      3      2      0     114       0   
170646  1.434152    113        4      2     10      8     450     782   
102714  1.725872    113        5      2     10     10     798    1730   
138365  0.000001    119        2      3      2      0     114       0   
7840    0.528823    113        9      2     52     42   37372    3380   

                rate  sttl  ...  ct_dst_ltm  ct_src_dport_ltm  \
41479   2.578214e+01   254  ...           2                 1   
174119  1.111111e+05   254  ...          15                15   
39585   6.461860e+01    31  ...          11                 1   
23269   2.832861e+03    31  ...           2                 1   
35227   7.324878e+01    31  ...           4                 1   
157804  3.333333e+05   254  ...          12                12   
170646  1.185370e+01    62  ...           2                 1   
102714  1.100893e+01    62  ...           1                 1   
138365  1.000000e+06   254  ...          16                16   
7840    1.758622e+02    31  ...           2                 1   

        ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
41479                  1               1             0           0   
174119                15              31             0           0   
39585                  1               5             0           0   
23269                  1               1             0           0   
35227                  1               5             1           1   
157804                12              14             0           0   
170646                 1               2             0           0   
102714                 1               1             0           0   
138365                16              18             0           0   
7840                   1               3             0           0   

        ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
41479                  0           1           5                0  
174119                 0          15          31                0  
39585                  0           3           6                0  
23269                  0           4           2                0  
35227                  0           6           2                0  
157804                 0          12          14                0  
170646                 0           4           1                0  
102714                 1           1           1                0  
138365                 0          16          18                0  
7840                   0           4           1                0  

[10 rows x 42 columns]

In [7]:
#min-max scaling
data_train_norm = (data_train - data_train.min()) / (data_train.max() - data_train.min())
data_train_norm = data_train_norm.fillna(0)

In [8]:
data_train_norm.shape
data_train_norm.head(10)

dur     proto   service     state     spkts     dpkts  \
41479   9.696635e-03  0.856061  0.000000  0.285714  0.000936  0.000553   
174119  1.500000e-07  0.901515  0.166667  0.428571  0.000104  0.000000   
39585   4.900551e-03  0.856061  0.333333  0.285714  0.000728  0.001106   
23269   1.765000e-05  0.901515  0.166667  0.000000  0.000104  0.000184   
35227   2.389119e-02  0.856061  0.250000  0.285714  0.005304  0.004977   
157804  5.000001e-08  0.901515  0.166667  0.428571  0.000104  0.000000   
170646  2.390254e-02  0.856061  0.333333  0.285714  0.000936  0.000737   
102714  2.876454e-02  0.856061  0.416667  0.285714  0.000936  0.000922   
138365  1.666667e-08  0.901515  0.166667  0.428571  0.000104  0.000000   
7840    8.813718e-03  0.856061  0.750000  0.285714  0.005304  0.003871   

          sbytes    dbytes      rate      sttl  ...  ct_dst_ltm  \
41479   0.000042  0.000018  0.000026  0.996078  ...        0.02   
174119  0.000005  0.000000  0.111111  0.996078  ...        0.28   
39585   0.000029  0.000609  0.000065  0.121569  ...        0.20   
23269   0.000008  0.000012  0.002833  0.121569  ...        0.02   
35227   0.000223  0.000258  0.000073  0.121569  ...        0.06   
157804  0.000005  0.000000  0.333333  0.996078  ...        0.22   
170646  0.000031  0.000054  0.000012  0.243137  ...        0.02   
102714  0.000058  0.000119  0.000011  0.243137  ...        0.00   
138365  0.000005  0.000000  1.000000  0.996078  ...        0.30   
7840    0.002879  0.000233  0.000176  0.121569  ...        0.02   

        ct_src_dport_ltm  ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  \
41479               0.00          0.000000        0.000000          0.00   
174119              0.28          0.311111        0.483871          0.00   
39585               0.00          0.000000        0.064516          0.00   
23269               0.00          0.000000        0.000000          0.00   
35227               0.00          0.000000        0.064516          0.25   
157804              0.22          0.244444        0.209677          0.00   
170646              0.00          0.000000        0.016129          0.00   
102714              0.00          0.000000        0.000000          0.00   
138365              0.30          0.333333        0.274194          0.00   
7840                0.00          0.000000        0.032258          0.00   

        ct_ftp_cmd  ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
41479         0.00          0.000000    0.000000    0.065574              0.0  
174119        0.00          0.000000    0.237288    0.491803              0.0  
39585         0.00          0.000000    0.033898    0.081967              0.0  
23269         0.00          0.000000    0.050847    0.016393              0.0  
35227         0.25          0.000000    0.084746    0.016393              0.0  
157804        0.00          0.000000    0.186441    0.213115              0.0  
170646        0.00          0.000000    0.050847    0.000000              0.0  
102714        0.00          0.033333    0.000000    0.000000              0.0  
138365        0.00          0.000000    0.254237    0.278689              0.0  
7840          0.00          0.000000    0.050847    0.000000              0.0  

[10 rows x 42 columns]

In [9]:
train_X = torch.tensor(data_train_norm.values, dtype=torch.float32)
train_Y = torch.tensor(label_train.values, dtype=torch.long) 
train = TensorDataset(train_X, train_Y)

In [10]:
train_loader = DataLoader(train, batch_size=100, shuffle=True)
# drop_last = True

In [11]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(42, 850)
        self.fc2 = nn.Linear(850, 10)
        
    def forward(self, x):
        x = F.relu(self.fc1(x)) # ReLU: max(x, 0)
        x = self.fc2(x)
        # return F.log_softmax(x, dim=1)
        return x

model = Net()

In [12]:
print(torch.cuda.is_available())

True


In [13]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.to(device)
print(device)

cuda


In [14]:
criterion = nn.CrossEntropyLoss()

In [15]:
#optimizer = torch.optim.SGD(model.parameters(), lr=0.03)
optimizer = torch.optim.Adam(model.parameters(), lr=0.03)

In [16]:
model.train()

Net(
  (fc1): Linear(in_features=42, out_features=850, bias=True)
  (fc2): Linear(in_features=850, out_features=10, bias=True)
)

In [17]:
#Training the machine learning model
loss_list=[]
for epoch in range(100): #learning 100 times
    #total_loss = 0
    model.train()
    for train_x, train_y in train_loader:
        train_x, train_y = Variable(train_x), Variable(train_y)
        train_x = train_x.to(device)
        train_y = train_y.to(device)
        optimizer.zero_grad()
        output = model(train_x)
        loss = criterion(output, train_y)
        loss.backward()
        optimizer.step()
        loss_list.append(loss.data)
        print('epoch {}, loss {}'.format(epoch, loss.item()))

epoch 0, loss 2.3339521884918213
epoch 0, loss 1.8054825067520142
epoch 0, loss 1.3487151861190796
epoch 0, loss 1.2773607969284058
epoch 0, loss 1.0959302186965942
epoch 0, loss 1.197260856628418
epoch 0, loss 0.8721634745597839
epoch 0, loss 0.7840537428855896
epoch 0, loss 0.9670166969299316
epoch 0, loss 1.2468433380126953
epoch 0, loss 0.9852697253227234
epoch 0, loss 0.8659031391143799
epoch 0, loss 0.8391802906990051
epoch 0, loss 1.0213111639022827
epoch 0, loss 0.9192003011703491
epoch 0, loss 0.863749623298645
epoch 0, loss 0.7514313459396362
epoch 0, loss 0.8112321496009827
epoch 0, loss 0.6443358063697815
epoch 0, loss 0.795512318611145
epoch 0, loss 0.8454355001449585
epoch 0, loss 0.7370989322662354
epoch 0, loss 0.9522980451583862
epoch 0, loss 0.6979246735572815
epoch 0, loss 0.7995240092277527
epoch 0, loss 0.6550685167312622
epoch 0, loss 0.6885824799537659
epoch 0, loss 0.802890956401825
epoch 0, loss 0.8374573588371277
epoch 0, loss 0.8696133494377136
epoch 0, loss 

epoch 0, loss 0.6772953867912292
epoch 0, loss 0.7993636131286621
epoch 0, loss 0.8287235498428345
epoch 0, loss 0.5995146036148071
epoch 0, loss 0.6776527166366577
epoch 0, loss 0.5838643312454224
epoch 0, loss 0.7698835730552673
epoch 0, loss 0.7945719957351685
epoch 0, loss 0.59600830078125
epoch 0, loss 0.6075013279914856
epoch 0, loss 0.5892828702926636
epoch 0, loss 0.5394197106361389
epoch 0, loss 0.807593822479248
epoch 0, loss 0.521943986415863
epoch 0, loss 0.7537577748298645
epoch 0, loss 0.7108964323997498
epoch 0, loss 0.6473343372344971
epoch 0, loss 0.5792020559310913
epoch 0, loss 0.696462094783783
epoch 0, loss 0.9293518662452698
epoch 0, loss 0.69423508644104
epoch 0, loss 0.5183279514312744
epoch 0, loss 0.6985791921615601
epoch 0, loss 0.7766783833503723
epoch 0, loss 0.8749528527259827
epoch 0, loss 0.7949836850166321
epoch 0, loss 0.7210883498191833
epoch 0, loss 0.6639657020568848
epoch 0, loss 0.6798376441001892
epoch 0, loss 0.7313011884689331
epoch 0, loss 0.6

epoch 0, loss 0.7398720383644104
epoch 0, loss 0.5714045166969299
epoch 0, loss 0.6012117862701416
epoch 0, loss 0.6408611536026001
epoch 0, loss 0.7020555734634399
epoch 0, loss 0.6642998456954956
epoch 0, loss 0.6443849205970764
epoch 0, loss 0.7207987904548645
epoch 0, loss 0.6690779328346252
epoch 0, loss 0.49733948707580566
epoch 0, loss 0.6069905757904053
epoch 0, loss 0.6759793758392334
epoch 0, loss 0.581188976764679
epoch 0, loss 0.528774619102478
epoch 0, loss 0.7381616234779358
epoch 0, loss 0.5630224943161011
epoch 0, loss 0.631199061870575
epoch 0, loss 0.6202571392059326
epoch 0, loss 0.5815882086753845
epoch 0, loss 0.641766369342804
epoch 0, loss 0.5277958512306213
epoch 0, loss 0.49759426712989807
epoch 0, loss 0.6709545254707336
epoch 0, loss 0.7403563857078552
epoch 0, loss 0.6157463192939758
epoch 0, loss 0.4633879065513611
epoch 0, loss 0.7524974942207336
epoch 0, loss 0.6912890672683716
epoch 0, loss 0.5199750661849976
epoch 0, loss 0.34477272629737854
epoch 0, lo

epoch 0, loss 0.5521066188812256
epoch 0, loss 0.5414226055145264
epoch 0, loss 0.5965281128883362
epoch 0, loss 0.7276695370674133
epoch 0, loss 0.48717689514160156
epoch 0, loss 0.5866898894309998
epoch 0, loss 0.4995117485523224
epoch 0, loss 0.6461691856384277
epoch 0, loss 0.6905697584152222
epoch 0, loss 0.6109420657157898
epoch 0, loss 0.5004743933677673
epoch 0, loss 0.6021646857261658
epoch 0, loss 0.5351669192314148
epoch 0, loss 0.6008413434028625
epoch 0, loss 0.5371650457382202
epoch 0, loss 0.6886448860168457
epoch 0, loss 0.708972692489624
epoch 0, loss 0.5896931886672974
epoch 0, loss 0.7828032970428467
epoch 0, loss 0.41870343685150146
epoch 0, loss 0.8311490416526794
epoch 0, loss 0.5424307584762573
epoch 0, loss 0.53817218542099
epoch 0, loss 0.6451876759529114
epoch 0, loss 0.6971458196640015
epoch 0, loss 0.547376811504364
epoch 0, loss 0.6082800030708313
epoch 0, loss 0.6314113736152649
epoch 0, loss 0.6180382966995239
epoch 0, loss 0.6716529130935669
epoch 0, los

epoch 0, loss 0.6569015383720398
epoch 0, loss 0.505729079246521
epoch 0, loss 0.43846166133880615
epoch 0, loss 0.5184500217437744
epoch 0, loss 0.6455078721046448
epoch 0, loss 0.7656812071800232
epoch 0, loss 0.550250768661499
epoch 0, loss 0.49820882081985474
epoch 0, loss 0.5854935646057129
epoch 0, loss 0.6665368676185608
epoch 0, loss 0.6216942071914673
epoch 0, loss 0.5217157602310181
epoch 0, loss 0.4966493248939514
epoch 0, loss 0.6030080318450928
epoch 0, loss 0.5128656625747681
epoch 0, loss 0.684884786605835
epoch 0, loss 0.49786272644996643
epoch 0, loss 0.5454358458518982
epoch 0, loss 0.5758058428764343
epoch 0, loss 0.47455811500549316
epoch 0, loss 0.5044558644294739
epoch 0, loss 0.7737364768981934
epoch 0, loss 0.5760836005210876
epoch 0, loss 0.8206468224525452
epoch 0, loss 0.758186399936676
epoch 0, loss 0.6815657019615173
epoch 0, loss 0.7854927182197571
epoch 0, loss 0.7746837139129639
epoch 0, loss 0.6081358790397644
epoch 0, loss 0.7672910094261169
epoch 0, l

...

epoch 98, loss 0.6127361059188843
epoch 98, loss 0.4933907687664032
epoch 98, loss 0.6260597705841064
epoch 98, loss 0.4496583044528961
epoch 98, loss 0.47390833497047424
epoch 98, loss 0.544279158115387
epoch 98, loss 0.7394751906394958
epoch 98, loss 0.5028247833251953
epoch 98, loss 0.5253666639328003
epoch 98, loss 0.7154079675674438
epoch 98, loss 0.6619403958320618
epoch 98, loss 0.5255125761032104
epoch 98, loss 0.6381614208221436
epoch 98, loss 0.5156418681144714
epoch 98, loss 0.41660186648368835
epoch 98, loss 0.438258558511734
epoch 98, loss 0.4114497900009155
epoch 98, loss 0.6034324765205383
epoch 98, loss 0.4062800109386444
epoch 98, loss 0.62920743227005
epoch 98, loss 0.5671746134757996
epoch 98, loss 0.4148791432380676
epoch 98, loss 0.4533202052116394
epoch 98, loss 0.5587883591651917
epoch 98, loss 0.6663659811019897
epoch 98, loss 0.5485309362411499
epoch 98, loss 0.5110915899276733
epoch 98, loss 0.4927577078342438
epoch 98, loss 0.48011451959609985
epoch 98, loss 

epoch 99, loss 0.4971533715724945
epoch 99, loss 0.5256231427192688
epoch 99, loss 0.7124563455581665
epoch 99, loss 0.45742127299308777
epoch 99, loss 0.4449812173843384
epoch 99, loss 0.5432083010673523
epoch 99, loss 0.6414220333099365
epoch 99, loss 0.5588737726211548
epoch 99, loss 0.5340003967285156
epoch 99, loss 0.6189289689064026
epoch 99, loss 0.43571966886520386
epoch 99, loss 0.6201784610748291
epoch 99, loss 0.3641893267631531
epoch 99, loss 0.47957244515419006
epoch 99, loss 0.5597916841506958
epoch 99, loss 0.4900203049182892
epoch 99, loss 0.6480876803398132
epoch 99, loss 0.4823168218135834
epoch 99, loss 0.6902136206626892
epoch 99, loss 0.3497284948825836
epoch 99, loss 0.48485618829727173
epoch 99, loss 0.4513225257396698
epoch 99, loss 0.5670487284660339
epoch 99, loss 0.40754836797714233
epoch 99, loss 0.4288572371006012
epoch 99, loss 0.45958787202835083
epoch 99, loss 0.5313229560852051
epoch 99, loss 0.5600500702857971
epoch 99, loss 0.3554711639881134
epoch 99

epoch 99, loss 0.5588629245758057
epoch 99, loss 0.3988398313522339
epoch 99, loss 0.6425562500953674
epoch 99, loss 0.6354773044586182
epoch 99, loss 0.5292496681213379
epoch 99, loss 0.5428007245063782
epoch 99, loss 0.5877055525779724
epoch 99, loss 0.44015371799468994
epoch 99, loss 0.5471827983856201
epoch 99, loss 0.6116735339164734
epoch 99, loss 0.5760219693183899
epoch 99, loss 0.6399788856506348
epoch 99, loss 0.4981660842895508
epoch 99, loss 0.4612429440021515
epoch 99, loss 0.6247748136520386
epoch 99, loss 0.6929812431335449
epoch 99, loss 0.4537058174610138
epoch 99, loss 0.5763161182403564
epoch 99, loss 0.5340557098388672
epoch 99, loss 0.45295578241348267
epoch 99, loss 0.5476702451705933
epoch 99, loss 0.565421462059021
epoch 99, loss 0.38502269983291626
epoch 99, loss 0.486800879240036
epoch 99, loss 0.38282445073127747
epoch 99, loss 0.47907784581184387
epoch 99, loss 0.46311119198799133
epoch 99, loss 0.4362415373325348
epoch 99, loss 0.5375916957855225
epoch 99, 

epoch 99, loss 0.49979957938194275
epoch 99, loss 0.5266066193580627
epoch 99, loss 0.3854497969150543
epoch 99, loss 0.5647908449172974
epoch 99, loss 0.47138363122940063
epoch 99, loss 0.462885320186615
epoch 99, loss 0.43360692262649536
epoch 99, loss 0.30942487716674805
epoch 99, loss 0.6519519686698914
epoch 99, loss 0.4655967354774475
epoch 99, loss 0.42661669850349426
epoch 99, loss 0.5243788957595825
epoch 99, loss 0.5484194755554199
epoch 99, loss 0.4502057135105133
epoch 99, loss 0.5912341475486755
epoch 99, loss 0.4711434543132782
epoch 99, loss 0.846785306930542
epoch 99, loss 0.49152567982673645
epoch 99, loss 0.48340487480163574
epoch 99, loss 0.6032603979110718
epoch 99, loss 0.5052127242088318
epoch 99, loss 0.6203007698059082
epoch 99, loss 0.5329629778862
epoch 99, loss 0.5149195194244385
epoch 99, loss 0.59324049949646
epoch 99, loss 0.44663363695144653
epoch 99, loss 0.5186078548431396
epoch 99, loss 0.4116148352622986
epoch 99, loss 0.4056614935398102
epoch 99, los

epoch 99, loss 0.5287190675735474
epoch 99, loss 0.5836566090583801
epoch 99, loss 0.4500937759876251
epoch 99, loss 0.5845316052436829
epoch 99, loss 0.4473264813423157
epoch 99, loss 0.4766375720500946
epoch 99, loss 0.38722991943359375
epoch 99, loss 0.6977154612541199
epoch 99, loss 0.6394491791725159
epoch 99, loss 0.4786592423915863
epoch 99, loss 0.4452381432056427
epoch 99, loss 0.6583969593048096
epoch 99, loss 0.4993772506713867
epoch 99, loss 0.5290747284889221
epoch 99, loss 0.49767792224884033
epoch 99, loss 0.44526463747024536
epoch 99, loss 0.512662410736084
epoch 99, loss 0.6051774621009827
epoch 99, loss 0.47058606147766113
epoch 99, loss 0.44500231742858887
epoch 99, loss 0.40398281812667847
epoch 99, loss 0.5196424722671509
epoch 99, loss 0.5499053001403809
epoch 99, loss 0.5489755868911743
epoch 99, loss 0.45107901096343994
epoch 99, loss 0.43805423378944397
epoch 99, loss 0.5114976167678833
epoch 99, loss 0.6128577589988708
epoch 99, loss 0.590038537979126
epoch 99

In [18]:
#Calculating correct_rate using the training data
pred_list = list()
test_y_list = list()
with torch.no_grad():
    model.eval()
    correct = 0
    for test_x, test_y in train_loader:
        test_y_list.extend(test_y.to('cpu').detach().numpy().tolist())
        test_x, test_y = Variable(test_x), Variable(test_y)
        test_x = test_x.to(device)
        test_y = test_y.to(device)
        output = model(test_x)
        pred = torch.max(output.data, 1)[1]
        #print(pred)
        pred_list.extend(pred.to('cpu').detach().numpy().tolist())
        correct += pred.eq(test_y.data.view_as(pred)).sum() 
    # correct_rate
    data_num = len(train_loader.dataset)
    print('correct _rate: {}/{} ({:.0f}%)\n'.format(correct, data_num, 100. * correct / data_num))

correct _rate: 98168/122738 (80%)



In [19]:
testdata = df_test.drop(['id', 'label', 'attack_cat'], axis=1)
testlabel = df_test.iloc[:,-2]

#min-max scaling
testdata_norm = (testdata - testdata.min()) / (testdata.max() - testdata.min())
testdata_norm = testdata_norm.fillna(0)

testdata_norm.head(10)

dur     proto   service  state     spkts     dpkts    sbytes  \
87395   1.928715e-02  0.856061  0.416667  0.250  0.000948  0.000729  0.000074   
171525  6.666668e-08  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
100997  3.536851e-03  0.856061  0.000000  0.000  0.000527  0.000182  0.000076   
106304  1.500000e-07  0.909091  0.000000  0.375  0.000105  0.000000  0.000014   
170606  1.929705e-02  0.856061  0.416667  0.250  0.000948  0.000729  0.000040   
113031  1.333334e-07  0.901515  0.000000  0.375  0.000105  0.000000  0.000011   
70458   1.333334e-07  0.022727  0.000000  0.375  0.000105  0.000000  0.000014   
138025  1.500000e-07  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
135044  1.166667e-07  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
161530  5.000001e-08  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   

          dbytes      rate      sttl  ...  ct_dst_ltm  ct_src_dport_ltm  \
87395   0.000024  0.000015  0.996078  ...        0.00              0.00   
171525  0.000000  0.250000  0.996078  ...        0.28              0.26   
100997  0.000006  0.000033  0.243137  ...        0.06              0.06   
106304  0.000000  0.111111  0.996078  ...        0.04              0.04   
170606  0.000024  0.000015  0.996078  ...        0.00              0.02   
113031  0.000000  0.125000  0.996078  ...        0.00              0.00   
70458   0.000000  0.125000  0.996078  ...        0.02              0.02   
138025  0.000000  0.111111  0.996078  ...        0.54              0.52   
135044  0.000000  0.142857  0.996078  ...        0.30              0.30   
161530  0.000000  0.333333  0.996078  ...        0.06              0.06   

        ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
87395           0.000000        0.062500           0.0         0.0   
171525          0.288889        0.203125           0.0         0.0   
100997          0.000000        0.093750           0.0         0.0   
106304          0.044444        0.046875           0.0         0.0   
170606          0.000000        0.000000           0.0         0.0   
113031          0.000000        0.000000           0.0         0.0   
70458           0.022222        0.031250           0.0         0.0   
138025          0.266667        0.406250           0.0         0.0   
135044          0.333333        0.375000           0.0         0.0   
161530          0.066667        0.296875           0.0         0.0   

        ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
87395           0.000000        0.00    0.000000              0.0  
171525          0.000000        0.26    0.213115              0.0  
100997          0.000000        0.08    0.098361              0.0  
106304          0.000000        0.04    0.049180              0.0  
170606          0.033333        0.36    0.000000              0.0  
113031          0.000000        0.02    0.016393              0.0  
70458           0.000000        0.04    0.032787              0.0  
138025          0.000000        0.52    0.426230              0.0  
135044          0.000000        0.32    0.393443              0.0  
161530          0.000000        0.06    0.311475              0.0  

[10 rows x 42 columns]

In [20]:
test_X = torch.tensor(testdata_norm.values, dtype=torch.float32)
test_Y = torch.tensor(testlabel.values, dtype=torch.long) 

test = TensorDataset(test_X, test_Y)
test_loader = DataLoader(test, batch_size=4096)

In [21]:
with torch.no_grad():
    model.eval()
    correct = 0
    pred_list = list()
    test_y_list = list()
    for test_x, test_y in test_loader:
        test_x, test_y = Variable(test_x), Variable(test_y)
        test_y_list.extend(test_y.to('cpu').detach().numpy().tolist())
        test_x = test_x.to(device)
        test_y = test_y.to(device)
        output = model(test_x)
        pred = torch.max(output.data, 1)[1]
        pred_list.extend(pred.to('cpu').detach().numpy().tolist())
        correct += pred.eq(test_y.data.view_as(pred)).sum() 
    # correct_rate
    data_num = len(test_loader.dataset)
    print('correct _rate: {}/{} ({:.0f}%)\n'.format(correct, data_num, 100. * correct / data_num))

correct _rate: 41150/52603 (78%)



In [22]:
accuracy_score(test_y_list, pred_list)

0.7822747752029352

In [23]:
precision_score(test_y_list, pred_list, average='macro')

C:\Users\hirot\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


0.541428883544435

In [24]:
recall_score(test_y_list, pred_list, average='macro')

0.49489924777665467

In [25]:
f1_score(test_y_list, pred_list, average='macro')

0.47717609306254516

In [26]:
cm = confusion_matrix(test_y_list, pred_list, labels=[0,1,2,3,4,5,6,7,8,9])
print(cm)

[[  125     0    27   416     2     0    30     8     4     0]
 [    0    19    26   427     4     0     0    31    13     0]
 [   20     5   287  3135    51    14    16    77    94     0]
 [  207     2   672  8132   306    23    61   603   116     0]
 [   10     0    42   680  3245     4  1072   214    72     0]
 [    7     0    10   200    32 11848     1    15     8     0]
 [  141     0    10   154  1409     4 14857    84    33     0]
 [    3     0    41   557    19     5    40  2445    16     0]
 [    0     0     6    42    31     0     8    58   192     0]
 [    2     0     0    17     2     2     0     9     3     0]]
